In [1]:
import os
import pandas as pd
from sklearn.model_selection import train_test_split, cross_validate
from sklearn.preprocessing import StandardScaler, MaxAbsScaler
from sklearn.decomposition import PCA
from sklearn.tree import DecisionTreeClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.ensemble import RandomForestClassifier
from sklearn.gaussian_process import GaussianProcessClassifier
from sklearn.neural_network import MLPClassifier
from sklearn.svm import SVC, LinearSVC
from sklearn.pipeline import Pipeline
from sklearn.metrics import precision_score, recall_score, f1_score, accuracy_score, classification_report

In [2]:
#read in data
target_file = r"C:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trading\data\interim\A_targets.csv"
data_file = r"C:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trading\data\interim\A_all_indicators_one_day.csv"
targets = pd.read_csv(target_file)
data = pd.read_csv(data_file)

In [3]:
#set target and data index to date
data['date'] = pd.to_datetime(data.date)
targets['date'] = pd.to_datetime(targets.date)
data = data.set_index(data.date)
targets = targets.set_index(targets.date)

In [4]:
#make function that aligns train data and target data
def merge_target_and_data(data_df, target_df, target_col):
    targets = target_df[[target_col]]
    data_df = data_df.merge(targets, 
                            how='left',
                            left_index=True,
                            right_index=True)
    data_df = data_df.dropna(subset=target_col)
    data_df = data_df.drop('date', axis=1)
    data_df = data_df.fillna(0)
    return data_df

In [5]:
test = merge_target_and_data(data, targets, '0.1%_higher_0.05%_drawdown_28')

In [6]:
def make_test_train_holdout(df, train_pct, holdout_size, target_col):
    #make train, test, and val
    total_length = df.shape[0]
    train_end = round(train_pct*total_length)
    train = df.iloc[0:train_end,:]
    test = df.iloc[train_end:-holdout_size,:]
    val = df.iloc[-holdout_size:,:]

    #split train, test, val into x,y
    train_x = train.drop(target_col, axis=1)
    train_y = train[[target_col]]

    test_x = test.drop(target_col, axis=1)
    test_y = test[[target_col]]

    # val_x = val.drop(target_col, axis=1)
    # val_y = val[[target_col]]

    return train_x, train_y, test_x, test_y#, val_x, val_y
    

In [7]:
def calculate_metrics(y_true, y_pred):
    accuracy = accuracy_score(y_true, y_pred)
    recall = recall_score(y_true, y_pred)
    precision = precision_score(y_true, y_pred)
    f1 = f1_score(y_true, y_pred)
    return accuracy, recall, precision, f1

In [8]:
#train_x, train_y, test_x, test_y = make_test_train_holdout(test, .4, 30, '0.1%_higher_0.05%_drawdown_28')

In [9]:
def data_end_to_end(target_file, feature_file, target_col, holdout, test_size):
    #read in data
    targets = pd.read_csv(target_file)
    data = pd.read_csv(feature_file)

    #convert date column to datetime and set as index
    data['date'] = pd.to_datetime(data.date)
    targets['date'] = pd.to_datetime(targets.date)
    data = data.set_index(data.date)
    targets = targets.set_index(targets.date)

    #merge targets and features
    combined = merge_target_and_data(data, targets, target_col)

    #make X and y arrays
    x = combined.drop(target_col, axis=1)
    y = combined[[target_col]]

    #make validation arrays
    val_x = x.iloc[-holdout:,:]
    val_y = y.iloc[-holdout:,:]

    #make train test
    train_x, test_x, train_y, test_y = train_test_split(x, y, test_size=test_size, stratify=y)

    return train_x, test_x, train_y, test_y, val_x, val_y

In [10]:
#get all binary target columns
target_columns = [x for x in targets.columns if "drawdown" in x]

In [11]:
models = [
    RandomForestClassifier(),
    LogisticRegression(),
    MLPClassifier(),
    GaussianProcessClassifier(),
    DecisionTreeClassifier(),
    SVC(),
    LinearSVC()
]

In [12]:
#get all feature and target files
INTERIM_DIR = r"C:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trading\data\interim"
feature_files = [x for x in os.listdir(INTERIM_DIR) if "indicators" in x]
target_files = [x for x in os.listdir(INTERIM_DIR) if "targets" in x]
holdout = 100

#iterate over all stocks and categorical targets and model, capture outputs
results = []
failures = []
for tgt_col in target_columns:
    for data, targets in zip(feature_files, target_files):
        try:
            stock = targets.split('_')[0]
            target_file = os.path.join(INTERIM_DIR, targets)
            feature_file = os.path.join(INTERIM_DIR, data)
            train_x, test_x, train_y, test_y, val_x, val_y = data_end_to_end(target_file,
                                                                            feature_file,
                                                                            tgt_col,
                                                                            holdout,
                                                                            test_size=.33)
            #iterate over models train and capture results
            for model in models:
                pipe = Pipeline([('scaler',StandardScaler()),
                                ('dim_reduction', PCA(n_components=.95)),
                                ('classifier', model)])
                
                pipe = pipe.fit(train_x, train_y)
                train_predictions = pipe.predict(train_x)
                test_predictions = pipe.predict(test_x)
                val_predictions = pipe.predict(val_x)
                model_name = pipe.steps[-1][1].__repr__()
                train_accuracy, train_precision, train_recall, train_f1 = calculate_metrics(train_y, train_predictions)
                test_accuracy, test_precision, test_recall, test_f1 = calculate_metrics(test_y, test_predictions)
                val_accuracy, val_precision, val_recall, val_f1 = calculate_metrics(val_y, val_predictions)
                train_results = (model_name, stock, tgt_col, "train", train_accuracy, train_precision, train_recall, train_f1)
                test_results = (model_name, stock, tgt_col, "test", test_accuracy, test_precision, test_recall, test_f1)
                val_results = (model_name, stock, tgt_col, "val", val_accuracy, val_precision, val_recall, val_f1)
                results.append(train_results)
                results.append(test_results)
                results.append(val_results)
                print('\n'*3)
                print('*'*80)
                print(f"{model_name}:{stock}:{tgt_col}")
                print("Train Classification Report\n")
                print(classification_report(train_y, train_predictions))
                print('\n'*2)
                print("Test Classification Report")
                print(classification_report(test_y, test_predictions))
                print('\n'*2)
                print("Val Classification Report")
                print(classification_report(val_y, val_predictions))
                print('*'*80)
                print('\n'*3)
        except:
            failures.append((stock,tgt_col))

            

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\base.py:1152: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)






********************************************************************************
RandomForestClassifier():AAL:0.05%_higher_0.025%_drawdown_7
Train Classification Report

              precision    recall  f1-score   support

         0.0       1.00      1.00      1.00       626
         1.0       1.00      1.00      1.00       212

    accuracy                           1.00       838
   macro avg       1.00      1.00      1.00       838
weighted avg       1.00      1.00      1.00       838




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.76      0.99      0.86       309
         1.0       0.75      0.09      0.15       105

    accuracy                           0.76       414
   macro avg       0.76      0.54      0.51       414
weighted avg       0.76      0.76      0.68       414




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.94      1.00      0.97        83
    

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\utils\validation.py:1183: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\linear_model\_logistic.py:460: ConvergenceWarning: lbfgs failed to converge (status=1):
STOP: TOTAL NO. of ITERATIONS REACHED LIMIT.

Increase the number of iterations (max_iter) or scale the data as shown in:
    https://scikit-learn.org/stable/modules/preprocessing.html
Please also refer to the documentation for alternative solver options:
    https://scikit-learn.org/stable/modules/linear_model.html#logistic-regression
  n_iter_i = _check_optimize_result(






********************************************************************************
LogisticRegression():AAL:0.05%_higher_0.025%_drawdown_7
Train Classification Report

              precision    recall  f1-score   support

         0.0       0.78      0.96      0.86       626
         1.0       0.63      0.22      0.32       212

    accuracy                           0.77       838
   macro avg       0.71      0.59      0.59       838
weighted avg       0.74      0.77      0.73       838




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.77      0.89      0.83       309
         1.0       0.40      0.21      0.28       105

    accuracy                           0.72       414
   macro avg       0.58      0.55      0.55       414
weighted avg       0.68      0.72      0.69       414




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.84      1.00      0.91        83
        

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:1102: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


...

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\base.py:1152: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modi





********************************************************************************
RandomForestClassifier():SNA:0.05%_higher_0.025%_drawdown_7
Train Classification Report

              precision    recall  f1-score   support

         0.0       1.00      1.00      1.00       754
         1.0       1.00      1.00      1.00        84

    accuracy                           1.00       838
   macro avg       1.00      1.00      1.00       838
weighted avg       1.00      1.00      1.00       838




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.90      1.00      0.95       371
         1.0       0.00      0.00      0.00        42

    accuracy                           0.90       413
   macro avg       0.45      0.50      0.47       413
weighted avg       0.81      0.90      0.85       413




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.98      1.00      0.99        97
    

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\utils\validation.py:1183: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))






********************************************************************************
LogisticRegression():SNA:0.05%_higher_0.025%_drawdown_7
Train Classification Report

              precision    recall  f1-score   support

         0.0       0.91      0.99      0.95       754
         1.0       0.60      0.07      0.13        84

    accuracy                           0.90       838
   macro avg       0.75      0.53      0.54       838
weighted avg       0.88      0.90      0.87       838




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.90      0.99      0.94       371
         1.0       0.25      0.02      0.04        42

    accuracy                           0.89       413
   macro avg       0.57      0.51      0.49       413
weighted avg       0.83      0.89      0.85       413




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.97      1.00      0.98        97
        

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_div

In [18]:
outputs = pd.DataFrame(data=results, columns=['model','stock','tgt','split','accuracy','precision','recall','f1'])

In [23]:
output_dir = r"C:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trading\data\processed"
output_name = os.path.join(output_dir,"first_results.xlsx")
outputs.to_csv(os.path.join(output_dir,'first_results.csv'))

In [304]:
holdout = 100
x = test.drop('0.1%_higher_0.05%_drawdown_28', axis=1)
y = test[['0.1%_higher_0.05%_drawdown_28']]

val_x = x.iloc[-holdout:,:]
val_y = y.iloc[-holdout:,:]

x = x.iloc[:-holdout,:]
y = y.iloc[:-holdout,:]

train_x, test_x, train_y, test_y = train_test_split(x, y, test_size=.33, stratify=y)


In [305]:
models = [
    RandomForestClassifier(),
    LogisticRegression(),
    MLPClassifier(),
    GaussianProcessClassifier(),
    DecisionTreeClassifier(),
    SVC(),
    LinearSVC()
]

In [306]:
#train an instance of each model and get performance metrics
results = []
for model in models:
    pipe = Pipeline([('scaler',StandardScaler()),
                    ('dim_reduction', PCA(n_components=.95)),
                    ('classifier', model)])
    
    pipe = pipe.fit(train_x, train_y)
    train_predictions = pipe.predict(train_x)
    test_predictions = pipe.predict(test_x)
    val_predictions = pipe.predict(val_x)
    model_name = pipe.steps[-1][1].__repr__()
    train_accuracy, train_precision, train_recall, train_f1 = calculate_metrics(train_y, train_predictions)
    test_accuracy, test_precision, test_recall, test_f1 = calculate_metrics(test_y, test_predictions)
    val_accuracy, val_precision, val_recall, val_f1 = calculate_metrics(val_y, val_predictions)
    train_results = (model_name, "train", train_accuracy, train_precision, train_recall, train_f1)
    test_results = (model_name, "test", test_accuracy, test_precision, test_recall, test_f1)
    val_results = (model_name, "val", val_accuracy, val_precision, val_recall, val_f1)
    results.append(train_results)
    results.append(test_results)
    results.append(val_results)
    print(model_name)
    print('*'*20)
    print("Train Classification Report\n")
    print(classification_report(train_y, train_predictions))
    print('\n'*2)
    print("Test Classification Report")
    print(classification_report(test_y, test_predictions))
    print('\n'*2)
    print("Val Classification Report")
    print(classification_report(val_y, val_predictions))
    print('\n'*2)


c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\base.py:1152: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples,), for example using ravel().
  return fit_method(estimator, *args, **kwargs)
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modi

RandomForestClassifier()
********************
Train Classification Report

              precision    recall  f1-score   support

         0.0       1.00      1.00      1.00       652
         1.0       1.00      1.00      1.00       105

    accuracy                           1.00       757
   macro avg       1.00      1.00      1.00       757
weighted avg       1.00      1.00      1.00       757




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.86      1.00      0.93       322
         1.0       1.00      0.02      0.04        52

    accuracy                           0.86       374
   macro avg       0.93      0.51      0.48       374
weighted avg       0.88      0.86      0.80       374




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.75      1.00      0.86        75
         1.0       0.00      0.00      0.00        25

    accuracy                           0.75     

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:1102: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\utils\validation.py:1183: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)


MLPClassifier()
********************
Train Classification Report

              precision    recall  f1-score   support

         0.0       0.99      1.00      1.00       652
         1.0       1.00      0.96      0.98       105

    accuracy                           0.99       757
   macro avg       1.00      0.98      0.99       757
weighted avg       0.99      0.99      0.99       757




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.90      0.96      0.93       322
         1.0       0.58      0.37      0.45        52

    accuracy                           0.87       374
   macro avg       0.74      0.66      0.69       374
weighted avg       0.86      0.87      0.86       374




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.76      0.87      0.81        75
         1.0       0.33      0.20      0.25        25

    accuracy                           0.70       100
   

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\utils\validation.py:1183: DataConversionWarning: A column-vector y was passed when a 1d array was expected. Please change the shape of y to (n_samples, ), for example using ravel().
  y = column_or_1d(y, warn=True)
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision is ill-defined and being set to 0.0 due to no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))


SVC()
********************
Train Classification Report

              precision    recall  f1-score   support

         0.0       0.89      1.00      0.94       652
         1.0       1.00      0.24      0.38       105

    accuracy                           0.89       757
   macro avg       0.95      0.62      0.66       757
weighted avg       0.91      0.89      0.86       757




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.87      1.00      0.93       322
         1.0       1.00      0.06      0.11        52

    accuracy                           0.87       374
   macro avg       0.93      0.53      0.52       374
weighted avg       0.89      0.87      0.82       374




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.75      1.00      0.86        75
         1.0       0.00      0.00      0.00        25

    accuracy                           0.75       100
   macro avg 

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_division` parameter to control this behavior.
  _warn_prf(average, modifier, msg_start, len(result))
c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\metrics\_classification.py:1471: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples. Use `zero_div

LinearSVC()
********************
Train Classification Report

              precision    recall  f1-score   support

         0.0       0.88      0.99      0.93       652
         1.0       0.73      0.18      0.29       105

    accuracy                           0.88       757
   macro avg       0.81      0.59      0.61       757
weighted avg       0.86      0.88      0.84       757




Test Classification Report
              precision    recall  f1-score   support

         0.0       0.87      0.97      0.92       322
         1.0       0.39      0.13      0.20        52

    accuracy                           0.85       374
   macro avg       0.63      0.55      0.56       374
weighted avg       0.81      0.85      0.82       374




Val Classification Report
              precision    recall  f1-score   support

         0.0       0.76      0.97      0.85        75
         1.0       0.50      0.08      0.14        25

    accuracy                           0.75       100
   macr

c:\Users\aburtnerabt\Documents\Continuing Education\Algo Trading\algo_trade\lib\site-packages\sklearn\svm\_base.py:1250: ConvergenceWarning: Liblinear failed to converge, increase the number of iterations.
  warnings.warn(


In [15]:
ouputs = pd.DataFrame(data=results, columns=['model','split','accuracy','precision','recall','f1'])

ValueError: 6 columns passed, passed data had 7 columns

In [249]:
#make pipeline
estimators = [('scaler', StandardScaler()),
              ('dim_reduction', PCA(n_components=.95)),
              ('classifier', DecisionTreeClassifier(max_depth=10, min_samples_leaf=20))]
pipe = Pipeline(estimators)
pipe = pipe.fit(train_x, train_y)
train_predictions = pipe.predict(train_x)
print(classification_report(train_y, train_predictions))

              precision    recall  f1-score   support

         0.0       0.92      0.95      0.94       419
         1.0       0.65      0.53      0.59        73

    accuracy                           0.89       492
   macro avg       0.79      0.74      0.76       492
weighted avg       0.88      0.89      0.88       492



In [250]:
test_predictions = pipe.predict(test_x)
scores = calculate_metrics(test_y, test_predictions)
print(f"Accuracy: {scores[0]:.04f}\tRecall: {scores[1]:.04f}\tPrecision: {scores[2]:.04f}\tF1: {scores[3]:.04f}")
print(classification_report(test_y, test_predictions))

Accuracy: 0.8106	Recall: 0.1193	Precision: 0.2281	F1: 0.1566
              precision    recall  f1-score   support

         0.0       0.86      0.93      0.89       630
         1.0       0.23      0.12      0.16       109

    accuracy                           0.81       739
   macro avg       0.54      0.52      0.52       739
weighted avg       0.77      0.81      0.78       739



In [251]:
val_predictions = pipe.predict(val_x)
scores = calculate_metrics(val_y, val_predictions)
print(f"Accuracy: {scores[0]:.04f}\tRecall: {scores[1]:.04f}\tPrecision: {scores[2]:.04f}\tF1: {scores[3]:.04f}")
print(classification_report(val_y, val_predictions))

Accuracy: 0.2000	Recall: 0.0800	Precision: 0.6667	F1: 0.1429
              precision    recall  f1-score   support

         0.0       0.15      0.80      0.25         5
         1.0       0.67      0.08      0.14        25

    accuracy                           0.20        30
   macro avg       0.41      0.44      0.20        30
weighted avg       0.58      0.20      0.16        30



In [13]:
nulls = test_x.isnull().sum()